In [1]:
import pandas as pd # for DataFrame manipulations
import scrapy    # for scraper

In [2]:
# build sample DataFrame with URLs
df = pd.DataFrame.from_dict({'URLs':['http://deposit.d-nb.de/cgi-bin/dokserv?id=4622549&prov=M&dok_var=1&dok_ext=htm',
                                     'http://deposit.d-nb.de/cgi-bin/dokserv?id=3838035&prov=M&dok_var=1&dok_ext=htm',
                                     'http://deposit.dnb.de/cgi-bin/dokserv?id=2771342&prov=M&dok_var=1&dok_ext=htm',
                                     'http://deposit.dnb.de/cgi-bin/dokserv?id=2745969&prov=M&dok_var=1&dok_ext=htm',
                                     'http://deposit.d-nb.de/cgi-bin/dokserv?id=4311298&prov=M&dok_var=1&dok_ext=htm',
                                     'http://www.vh-buchshop.de/vh-verlagsprogramm/elektro-html/ausbildung-elektroniker-installation-in-feuergefardeten-betriebsstatten.html',
                                     'http://www.vh-buchshop.de/vh-verlagsprogramm/elektro-html/ausbildung-elektroniker-knx.html',
                                     'http://deposit.d-nb.de/cgi-bin/dokserv?id=3948065&prov=M&dok_var=1&dok_ext=htm',
                                     'http://deposit.d-nb.de/cgi-bin/dokserv?id=4090655&prov=M&dok_var=1&dok_ext=htm',
                                     'http://deposit.d-nb.de/cgi-bin/dokserv?id=4032927&prov=M&dok_var=1&dok_ext=htm']
                            })
# display DataFrame
df.head()

URLs
0  http://deposit.d-nb.de/cgi-bin/dokserv?id=4622...
1  http://deposit.d-nb.de/cgi-bin/dokserv?id=3838...
2  http://deposit.dnb.de/cgi-bin/dokserv?id=27713...
3  http://deposit.dnb.de/cgi-bin/dokserv?id=27459...
4  http://deposit.d-nb.de/cgi-bin/dokserv?id=4311...

## Note!
Scraping seems to make some trouble, e.g. running the scraper cell (futher down) twice causes an error. I'd suggest to seperate the data_preprocessing from yesterday and the scraping. I would first try to save the processed DataFrame from yesterday to a pickle file and load it here in the scraper script.

See cell below how to save a DataFrame and load it again (here via pickle module - other data formats might work equally well)

In [3]:
import pandas as pd
    # save DataFrame to pkl format
    #df.to_pickle('bib.pkl')
    # delete df variable in Python - all info gone
    #del(df)
# load data from pkl file 
df = pd.read_pickle('../data/urls.pkl')
# display loaded info
df.loc[1,:].replace(' http','http')
df.loc[1,:]

URLs    http://deposit.d-nb.de/cgi-bin/dokserv?id=3838...
Name: 1, dtype: object

In [4]:
import scrapy
# get list of all URLs from DataFrame that need to be scraped:
URLs = list(df['URLs'])
# drop duplicates, e.g. a URL that appeas twice will only appear once afterwards
URLs = list(set(URLs))
URLs=URLs[1:]
# a buffer to save the ScraperResults
ScraperResults =  []

# define the webspider
class BibSpider(scrapy.Spider):
    ''' 
    webspider for bib scraping.
    currently supports *.deposit URLs
    '''
    # give spider access to some global variables
    global URLs, ScraperResults
    # name of our spider, optional
    name = "bib_scraper"
    # give the spider a list of URLs that need to be scraped / parsed
    start_urls = URLs


    def parse(self, response):
        ''' parser of webspider '''
        try:
            # tries to get the following results for each url
            res = {
                     "url": response.url,
                     "title": ' '.join(response.css('h3::text').getall()),
                     "content": ' '.join(response.css('p::text').getall())
                  }
            # saves the result of the scraping to Scraper Results
            ScraperResults.append(res)

        except Exception as E:
            # if the try block fails, we simply ignore the url
            pass

In [5]:
URLs[1:]

['http://deposit.d-nb.de/cgi-bin/dokserv?id=3245183&prov=M&dok_var=1&dok_ext=htm',
 'http://deposit.d-nb.de/cgi-bin/dokserv?id=3896861&prov=M&dok_var=1&dok_ext=htm',
 'http://deposit.d-nb.de/cgi-bin/dokserv?id=4050489&prov=M&dok%5Fvar=1&dok%5Fext=htm',
 'http://deposit.d-nb.de/cgi-bin/dokserv?id=3121062&prov=M&dok_var=1&dok_ext=htm',
 'http://deposit.d-nb.de/cgi-bin/dokserv?id=b1e11d697f26458d9ac1eec401347ef9&prov=M&dok_var=1&dok_ext=htm',
 'http://deposit.d-nb.de/cgi-bin/dokserv?id=5229648&prov=M&dok_var=1&dok_ext=htm',
 'http://deposit.d-nb.de/cgi-bin/dokserv?id=2966293&prov=M&dok_var=1&dok_ext=htm',
 'http://deposit.d-nb.de/cgi-bin/dokserv?id=3ddc8084fb5a426fb78421d872563fed&prov=M&dok_var=1&dok_ext=htm',
 'http://deposit.dnb.de/cgi-bin/dokserv?id=2646369&prov=M&dok_var=1&dok_ext=htm',
 'http://deposit.d-nb.de/cgi-bin/dokserv?id=4533260&prov=M&dok_var=1&dok_ext=htm',
 'http://deposit.dnb.de/cgi-bin/dokserv?id=07e8fa7b72564977ab0dd32d7f5980e5&prov=M&dok_var=1&dok_ext=htm',
 'http://d

In [6]:

from scrapy.crawler import CrawlerProcess

# this is how we can run the BibSpider in Jupyter
# see https://stackoverflow.com/questions/13437402/how-to-run-scrapy-from-within-a-python-script
process = CrawlerProcess({
    'USER_AGENT': 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)'
})
process.crawl(BibSpider)
process.start()
process.stop()

2020-04-30 20:41:24 [scrapy.utils.log] INFO: Scrapy 1.6.0 started (bot: scrapybot)
2020-04-30 20:41:24 [scrapy.utils.log] INFO: Versions: lxml 4.5.0.0, libxml2 2.9.9, cssselect 1.1.0, parsel 1.5.2, w3lib 1.21.0, Twisted 19.10.0, Python 3.7.4 (default, Aug  9 2019, 18:34:13) [MSC v.1915 64 bit (AMD64)], pyOpenSSL 19.1.0 (OpenSSL 1.1.1d  10 Sep 2019), cryptography 2.8, Platform Windows-10-10.0.18362-SP0
2020-04-30 20:41:24 [scrapy.crawler] INFO: Overridden settings: {'USER_AGENT': 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)'}
2020-04-30 20:41:24 [scrapy.extensions.telnet] INFO: Telnet Password: 05b829976ca6e5fe
2020-04-30 20:41:24 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.extensions.logstats.LogStats']
2020-04-30 20:41:24 [scrapy.middleware] INFO: Enabled downloader middlewares:
['scrapy.downloadermiddlewares.httpauth.HttpAuthMiddleware',
 'scrapy.downloadermiddlewares.downloadtimeou

2020-04-30 20:41:27 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3720865&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:27 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3404800&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:28 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3873734&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:28 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3243342&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:28 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=4706834&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:28 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.dnb.de/cgi-bin/dokserv?id=2646369&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:28 [sc

2020-04-30 20:41:30 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=4568181&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:31 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=90645f1b2a2846f99ef99271b49e207e&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:31 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=2957412&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:31 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3323568&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:31 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3067523&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:31 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3126333&prov=M&dok_var=1&dok_ext=htm> (referer: Non

2020-04-30 20:41:33 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=4388376&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=4572087&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3629741&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=2851941&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3496472&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=2854299&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:34 [s

2020-04-30 20:41:37 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=2897470&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:37 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=4836675&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:37 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.dnb.de/cgi-bin/dokserv?id=2815386&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:37 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=4422643&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:37 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=5145785&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 20:41:37 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.dnb.de/cgi-bin/dokserv?id=bdb6514818fc42b294a2654bb423c115&prov=M&dok_var=1&dok_ext=htm> (referer: None)

...

2020-04-30 21:05:50 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3878913&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:05:50 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=44610be54efe4eff822444c272b87144&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:05:50 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=2840916&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:05:50 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.dnb.de/cgi-bin/dokserv?id=2657616&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:05:50 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=4164129&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:05:50 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=4529885&prov=M&dok%5Fvar=1&dok%5Fext=htm> (referer: 

2020-04-30 21:05:53 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3164813&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:05:53 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3045713&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:05:53 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=4653620&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:05:53 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3785011&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:05:54 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3922450&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:05:54 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.dnb.de/cgi-bin/dokserv?id=ee7b403a55f34ef5b7f5f74dbe88cc16&prov=M&dok_var=1&dok_ext=htm> (referer: None

2020-04-30 21:05:56 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3073666&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:05:57 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=2964491&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:05:57 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.dnb.de/cgi-bin/dokserv?id=2749366&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:05:57 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3670255&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:05:57 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.dnb.de/cgi-bin/dokserv?id=2753813&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:05:57 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=5290043&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:05:57 [scr

2020-04-30 21:05:59 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=4115989&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:06:00 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3237598&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:06:00 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=4662253&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:06:00 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3819506&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:06:00 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=3708395&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:06:00 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://deposit.d-nb.de/cgi-bin/dokserv?id=4501233&prov=M&dok_var=1&dok_ext=htm> (referer: None)
2020-04-30 21:06:00 [s

<DeferredList at 0x1d59c88e648 current result: []>

In [7]:
# pprint means pretty print - looks nicer for dictionaries
from pprint import pprint

# info on success of scraper
print('number of urls:',len(URLs))
print('number of results:',len(ScraperResults))
print('number of errors:',len(URLs)-len(ScraperResults),'\n')

# give some examples of scraping
# ! Note that the entries for 'content' etc. are actually one large string, ' .. ' come from pprint
print('some examples:')
pprint(ScraperResults[0:3])

number of urls: 23026
number of results: 22975
number of errors: 51 

some examples:
[{'content': 'Der Upload eines Fotos im Internet ist die wohl bequemste und '
             'gleichzeitig effektivste Möglichkeit, sich in kürzester Zeit '
             'einer Vielzahl Dritter zu offenbaren. Häufig stellt jedoch '
             'gerade dieser Fotoupload gleichzeitig eine '
             'Persönlichkeitsrechtsverletzung dar.  Die vorliegende '
             'Untersuchung zeigt dem Leser auf, wann der Drang nach Selbst- '
             'oder Fremddarstellung die Grenze der Zulässigkeit überschreitet '
             'und sensibilisiert ihn dahingehend, sich zukünftig rechtskonform '
             'zu verhalten. Plattformbetreibern wird gleichzeitig an die Hand '
             'gegeben, ihren Dienst so zu gestalten, dass Rechtsverletzungen '
             'bereits im Vorfeld entgegengewirkt wird. Schließlich werden auch '
             'Gesetzgeber und Rechtsprechung dahingehend in die Pflicht '
   

In [8]:
# we quickly rearrange the results in a more usable way 
# a "dictionary of dictionaries"

results = {}
for i in range(len(ScraperResults)):
    results[ScraperResults[i]['url']] = {'title':ScraperResults[i]['title'],
                                         'content':ScraperResults[i]['content']}

In [9]:
def get_title(url):
    ''' function returns title of url '''
    global results
    try:
        return results[url]['title']
    except:
        return 'scraper error'
    
def get_content(url):
    ''' function returns content of url '''
    global results
    try:
        return results[url]['content']
    except:
        return 'scraper error'

# fill columns of DataFrame with info from scraper
# "apply" applies a function to all rows in one column 
df['title']   = df['URLs'].apply(get_title)
df['content'] = df['URLs'].apply(get_content)
df.head(10)

URLs  \
1   http://deposit.d-nb.de/cgi-bin/dokserv?id=3838...   
2   http://deposit.dnb.de/cgi-bin/dokserv?id=27713...   
3   http://deposit.dnb.de/cgi-bin/dokserv?id=27459...   
4   http://deposit.d-nb.de/cgi-bin/dokserv?id=4311...   
7   http://deposit.d-nb.de/cgi-bin/dokserv?id=3948...   
8   http://deposit.d-nb.de/cgi-bin/dokserv?id=4090...   
9   http://deposit.d-nb.de/cgi-bin/dokserv?id=4032...   
10  http://deposit.d-nb.de/cgi-bin/dokserv?id=3842...   
11  http://deposit.d-nb.de/cgi-bin/dokserv?id=3125...   
12  http://deposit.d-nb.de/cgi-bin/dokserv?id=3932...   

                                                title  \
1                           Aernout Mik - Communitas    
2                        Anton Henning  : Dt. /Engl.    
3    Die Feuchtwangers  : Familie, Tradition und j...   
4    Grüne Philosophie  : Ein konservativer Denkan...   
7    Handwörterbuch des politischen Systems der Bu...   
8    Technische Dokumentation im Maschinen- und An...   
9      Geotechnik  : Bodenmechanik  / von Gerd Möller   
10   Farben  : Natur, Technik, Kunst  / von Norber...   
11        Stuff  : The Nature of Chemical Substances    
12          Geotechnik  : Grundbau  / von Gerd Möller   

                                              content  
1   Aernout Mik zählt zu den wichtigsten Künstlern...  
2   Die vorliegende Publikation widmet sich drei o...  
3   150 Jahre Geschichte deutsch-jüdischen Bürgert...  
4   Der Umweltschutz liegt herkömmlich im Hoheitsg...  
7   Dieses Buch bietet die Grundlagen zu allen wic...  
8   Das Buch gibt dem Anwender die entscheidenden ...  
9   Das Buch vermittelt alle wichtigen Aspekte übe...  
10  Mit Farben in der 3. Auflage gehen Welsch und ...  
11  J. Schummer: Matter versus Form, and Beyond – ...  
12  Das komplexe und technisch hoch spezialisierte...

In [10]:
df.describe()

URLs          title        content
count   23277          23277          23277
unique  23027          22556          22820
top            scraper error  scraper error
freq      195            287            287

In [11]:
# load data from pkl file 
df100 = pd.read_pickle('../data/df100.pkl')
# removes first row
df100 = df100.iloc[1:]
# display DataFrame
df100.head()

100                                                084
1             NaN                                  [Kunstgeschichte]
2             NaN                                                NaN
3   Specht, Heike                 [Sprachwissenschaften, Geschichte]
4  Scruton, Roger  [Allgemeines, Philosophie, Theologie und Relig...
7             NaN                                      [Politologie]

In [12]:
# join both dataframes
frames = [df, df100]
df2 = pd.concat((frames), axis=1, sort=True)
# rename column
df2.rename(columns={'100':'author'}, inplace=True)
df2.rename(columns={'084':'class'}, inplace=True)
#rearrange column, drop out URLs column
cols = df2.columns.tolist()
df2 = df2[['author', 'title', 'class', 'content']]

In [13]:
df2.head(20)

author                                              title  \
1                      NaN                          Aernout Mik - Communitas    
2                      NaN                       Anton Henning  : Dt. /Engl.    
3            Specht, Heike   Die Feuchtwangers  : Familie, Tradition und j...   
4           Scruton, Roger   Grüne Philosophie  : Ein konservativer Denkan...   
7                      NaN   Handwörterbuch des politischen Systems der Bu...   
8       Schlagowski, Heinz   Technische Dokumentation im Maschinen- und An...   
9             Möller, Gerd     Geotechnik  : Bodenmechanik  / von Gerd Möller   
10         Welsch, Norbert   Farben  : Natur, Technik, Kunst  / von Norber...   
11                     NaN        Stuff  : The Nature of Chemical Substances    
12            Möller, Gerd          Geotechnik  : Grundbau  / von Gerd Möller   
13                     NaN   Neue professionelle Schaltungstechniken  : Üb...   
15                     NaN   Partielle Differentialgleichungen  : Höhere M...   
16                     NaN   Nonporous Inorganic Membranes  : for Chemical...   
17   Matthies, Hans Jürgen   Einführung in die Ölhydraulik  ehem. unter Re...   
18           Thiedeke, Udo   Trust, but test!  : Das Vertrauen in virtuell...   
19                     NaN           Pragmatismus – Philosophie der Zukunft?    
20                     NaN   Handbuch Theorien und Methoden der Raum- und ...   
21  Fleischmann, Katharina   Stadt Land Gender  : Einführung in Feministis...   
22          Streit, Roy L.       Poisson Point Processes  / von Roy L. Streit   
23                     NaN     Modern Architecture in Berlin  / von Rolf Rave   

                                                class  \
1                                   [Kunstgeschichte]   
2                                                 NaN   
3                  [Sprachwissenschaften, Geschichte]   
4   [Allgemeines, Philosophie, Theologie und Relig...   
7                                       [Politologie]   
8                                           [Technik]   
9                                           [Technik]   
10             [Psychologie, Physik, Kunstgeschichte]   
11                                      [Philosophie]   
12                              [Geographie, Technik]   
13                                          [Technik]   
15                                       [Mathematik]   
16                                           [Chemie]   
17                                          [Technik]   
18                          [Allgemeines, Soziologie]   
19                                      [Philosophie]   
20                          [Geographie, Allgemeines]   
21               [Geographie, Soziologie, Ethnologie]   
22                                          [Technik]   
23                                                NaN   

                                              content  
1   Aernout Mik zählt zu den wichtigsten Künstlern...  
2   Die vorliegende Publikation widmet sich drei o...  
3   150 Jahre Geschichte deutsch-jüdischen Bürgert...  
4   Der Umweltschutz liegt herkömmlich im Hoheitsg...  
7   Dieses Buch bietet die Grundlagen zu allen wic...  
8   Das Buch gibt dem Anwender die entscheidenden ...  
9   Das Buch vermittelt alle wichtigen Aspekte übe...  
10  Mit Farben in der 3. Auflage gehen Welsch und ...  
11  J. Schummer: Matter versus Form, and Beyond – ...  
12  Das komplexe und technisch hoch spezialisierte...  
13  Sammelband aus: 300 neue professionelle Schalt...  
15  Grundlegende Räume - Lineare Operatoren in nor...  
16  This reference book addresses the evolution of...  
17  Grundlagen für Entwicklung und Betrieb ölhydra...  
18  »Trust, but test!« lautet ein Kernsatz der Hac...  
19  Vorwort der Herausgeber I. ZUR AKTUALITÄT DES ...  
20  In der Raum- und Umweltplanung gewinnen Planun...  
21  Hinsichtlich der Genderperspektive ein grundle...  
22  "Poisson Point Processes provides an overview ...  


In [14]:
# save scraped data to pickle and csv (the latter for taking a look with excel,
# the former for next steps in pyhton)
df2.to_pickle('../data/data_parsed_and_scraped.pkl')
df2.to_csv('../data/data_parsed_and_scraped.csv', sep=';', quotechar = '"')